<a href="https://colab.research.google.com/github/tanvi-ap/Covid19StanceDetection/blob/main/covid19stance_v1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

1. [COVID-19 Vaccine — What’s the Public Sentiment](https://towardsdatascience.com/covid-19-vaccine-whats-the-public-sentiment-7149c9b42b99)
2. [COVID-19 Sentiment Analysis Series](https://towardsdatascience.com/covid-19-sentiment-analysis-series-part-1-getting-started-70892122630c)

In [1]:
from google.colab import drive
drive.mount('/drive')

Mounted at /drive


In [ ]:
!pip install python-dotenv

In [ ]:
!pip install tweet-preprocessor

In [ ]:
!pip install stanza

     |████████████████████████████████| 432 kB 27.8 MB/s 
     |████████████████████████████████| 170 kB 69.4 MB/s 
  Created wheel for emoji: filename=emoji-1.6.1-py3-none-any.whl size=169314 sha256=b4b4ad170b37ec4e96f5ffe586104c18a4fde417146498c7ec816152f529e60c
  Stored in directory: /root/.cache/pip/wheels/ea/5f/d3/03d313ddb3c2a1a427bb4690f1621eea60fe6f2a30cc95940f
Successfully built emoji


In [ ]:
!pip install pycorenlp

  Created wheel for pycorenlp: filename=pycorenlp-0.3.0-py3-none-any.whl size=2143 sha256=bd378579c500f20b956349ae3beb063883d919435f3c18e7669283a6b07cbfad
  Stored in directory: /root/.cache/pip/wheels/83/d8/ad/6b2276343ac605ee47e6beddb28331e96377909e5c816539c3
Successfully built pycorenlp


In [ ]:
!pip install flair

In [2]:
# General dependencies
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import re
import os
import time
from datetime import datetime, date, timedelta

# For Twitter API extraction
import tweepy
#!pip install python-dotenv
#from dotenv import load_dotenv

# Tweet pre-processor
# import preprocessor as p

# # NLTK
# import nltk
# nltk.download('vader_lexicon')
# from nltk.sentiment.vader import SentimentIntensityAnalyzer

# # TextBlob
# from textblob import TextBlob

# # FLairNLP
# from flair.models import TextClassifier
# from flair.data import Sentence

# # Stanza
# import stanza
# stanza.download('en')

# # Stanford CoreNLP
# from pycorenlp import StanfordCoreNLP

import json

In [3]:

f= open('/drive/MyDrive/keys.json','r')
data = json.load(f)

#print(data[0])

In [5]:

auth = tweepy.OAuthHandler(data[0]['consumer_key'], data[0]['consumer_secret'])
auth.set_access_token(data[0]['access_token'], data[0]['access_secret'])
api = tweepy.API(auth,wait_on_rate_limit=True)


In [6]:
# Generate list of dates (7 days window) based on today's date
list_of_dates = []
today = date.today()
for i in range(-7,1):
    target_date = (today + timedelta(days=i)).strftime("%Y-%m-%d")
    list_of_dates.append(target_date)

In [7]:
list_of_dicts = []
search_term = 'covid19 covid vaccine coronavirus'
num_tweets = 16000

In [22]:
#https://github.com/kennethleungty/COVID19-Vaccine-Sentiment-Analysis/blob/main/COVID-19%20Vaccine%20Sentiment%20Analysis.ipynb
def get_tweets(search_term = search_term, num_tweets = num_tweets):
    
    for end_date in list_of_dates:
        start_date = (datetime.strptime(end_date, '%Y-%m-%d') - timedelta(days=1)).strftime("%Y-%m-%d")
        end_date=date.today()
        tweet_count = len(list_of_dicts)

        for tweet in tweepy.Cursor(api.search,
                                   q=f'{search_term} since:{start_date} until:{end_date}',
                                   lang = 'en',
                                   count = num_tweets,
                                   tweet_mode = 'extended').items(num_tweets):
            if (not tweet.retweeted) and ('RT @' not in tweet.full_text):
                if tweet.lang == "en":
                    tweet_dict = {}
                    tweet_dict['username'] = tweet.user.name
                    tweet_dict['location'] = tweet.user.location
                    tweet_dict['text'] = tweet.full_text
                    #tweet_dict['fav_count'] = tweet.favorite_count  
                    tweet_dict['hashtags'] = tweet.entities['hashtags']
                    tweet_dict['tweet_date'] = tweet.created_at
                    list_of_dicts.append(tweet_dict)
                    tweet_count +=1
                    print(f'Extracted tweet count = {tweet_count}')
                
        print(f'Completed extraction for {start_date} to {end_date}. Sleep for 15 mins')
        time.sleep(900)
        print('Ready to go again')

In [23]:
get_tweets()

Streaming output truncated to the last 5000 lines.
Extracted tweet count = 7933
Extracted tweet count = 7934
Extracted tweet count = 7935
Extracted tweet count = 7936
Extracted tweet count = 7937
Extracted tweet count = 7938
Extracted tweet count = 7939
Extracted tweet count = 7940
Extracted tweet count = 7941
Extracted tweet count = 7942
Extracted tweet count = 7943
Extracted tweet count = 7944
Extracted tweet count = 7945
Extracted tweet count = 7946
Extracted tweet count = 7947
Extracted tweet count = 7948
Extracted tweet count = 7949
Extracted tweet count = 7950
Extracted tweet count = 7951
Extracted tweet count = 7952
Extracted tweet count = 7953
Extracted tweet count = 7954
Extracted tweet count = 7955
Extracted tweet count = 7956
Extracted tweet count = 7957
Extracted tweet count = 7958
Extracted tweet count = 7959
Extracted tweet count = 7960
Extracted tweet count = 7961
Extracted tweet count = 7962
Extracted tweet count = 7963
Extracted tweet count = 7964
Extracted tweet count

In [24]:
len(list_of_dicts)

12916

In [25]:
# Transform list of dictionaries into a Pandas dataframe
tweets_df = pd.DataFrame(list_of_dicts)
tweets_df.sort_values(by='tweet_date').reset_index(drop = True)

username  ...          tweet_date
0           moneycontrol  ... 2021-11-19 04:26:12
1           moneycontrol  ... 2021-11-19 04:26:12
2      brian commonsense  ... 2021-11-19 04:40:25
3      brian commonsense  ... 2021-11-19 04:40:25
4           Caring Heart  ... 2021-11-19 04:44:11
...                  ...  ...                 ...
12911    Wicked Prepping  ... 2021-11-27 23:40:02
12912    Wicked Prepping  ... 2021-11-27 23:40:02
12913    Wicked Prepping  ... 2021-11-27 23:40:02
12914    Wicked Prepping  ... 2021-11-27 23:40:02
12915    Wicked Prepping  ... 2021-11-27 23:40:02

[12916 rows x 5 columns]

In [26]:
tweets_df.to_csv('/drive/MyDrive/climatechange_tweets.csv')

In [27]:
with open('/drive/MyDrive/climatechange_tweets.csv','r') as input:
  data = input.read()

data

',username,location,text,hashtags,tweet_date\n0,Wicked Prepping,,"Mandatory Vaccinations...\n           or Just Coercive Manipulation?\n\n😱Green Zones Coming to a Town Near You!\n\n---&gt; https://t.co/GQxOqL2aSg \n\n#Vaccine #Vaccinations #WEF #NWO #COVID19 #COVID #coronavirus #prepper #prepping","[{\'text\': \'Vaccine\', \'indices\': [144, 152]}, {\'text\': \'Vaccinations\', \'indices\': [153, 166]}, {\'text\': \'WEF\', \'indices\': [167, 171]}, {\'text\': \'NWO\', \'indices\': [172, 176]}, {\'text\': \'COVID19\', \'indices\': [177, 185]}, {\'text\': \'COVID\', \'indices\': [186, 192]}, {\'text\': \'coronavirus\', \'indices\': [193, 205]}, {\'text\': \'prepper\', \'indices\': [206, 214]}, {\'text\': \'prepping\', \'indices\': [215, 224]}]",2021-11-27 23:40:02\n1,WORLD UPDATES #coronavirus disease 2019 (COVID-19),United Kingdom,"UK.\n\nOn 27 November, 39,567 new cases and 131 deaths within 28 days of a positive test were reported across the UK.\n\nOur data includes the number of peopl

**Preprocessing**